In [ ]:
import os
import time
import pandas as pd
from datasets import load_dataset, DatasetDict
from together import Together
from dotenv import load_dotenv

load_dotenv()


client = Together(api_key=os.getenv("TOGETHER_API_KEY"))


In [ ]:
BASE_MODEL_ID = "deepseek-ai/DeepSeek-R1-Distill-Qwen-14B"
DATASET_ID = "boatbomber/Roblox-Luau-Reasoning-v1.0"
SYSTEM_PROMPT = "You are an expert Roblox developer and Luau software engineer."
COMPLETION_TEMPLATE = """\
<think>
{chain_of_thought}
</think>

```Lua
{code}
```

{explanation}\
"""


Build the fine tuning dataset

In [ ]:
DATASET_FILE_ID = "file-790ced3f-fbb4-46f4-87d7-cb5bf33b1623"
if not DATASET_FILE_ID:
    dataset_splits: DatasetDict = load_dataset(DATASET_ID)
    combined_df = pd.DataFrame(columns=["messages"])
    for split, dataset in dataset_splits.items():
        df: pd.DataFrame = dataset.to_pandas()
        df["messages"] = df.apply(
            lambda row: [
                {
                    "role": "system",
                    "content": SYSTEM_PROMPT,
                },
                {
                    "role": "user",
                    "content": row["prompt"],
                },
                {
                    "role": "assistant",
                    "content": COMPLETION_TEMPLATE.format(
                        chain_of_thought=row["chain_of_thought"],
                        code=row["code"],
                        explanation=row["explanation"],
                    ),
                },
            ],
            axis=1,
        )
        df = df[["messages"]]

        # Add prompt, completion from each row to the combined_df
        combined_df = pd.concat([combined_df, df], ignore_index=True)

    combined_df.to_json("cache/luau-reasoning.jsonl", orient="records", lines=True)
    file_resp = client.files.upload(file="cache/luau-reasoning.jsonl", check=True)

    print("DATASET_FILE_ID", file_resp.id)
    DATASET_FILE_ID = file_resp.id


train.parquet:   0%|          | 0.00/47.3M [00:00<?, ?B/s]

test.parquet:   0%|          | 0.00/9.77M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/15341 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/3254 [00:00<?, ? examples/s]

Uploading file luau-reasoning.jsonl: 100%|██████████| 132M/132M [00:11<00:00, 11.5MB/s] 


DATASET_FILE_ID file-790ced3f-fbb4-46f4-87d7-cb5bf33b1623


Trigger fine-tuning job

In [ ]:
FT_JOB_ID = "ft-49dc2cfb-959b"
if not FT_JOB_ID:
    job_resp = client.fine_tuning.create(
        training_file=DATASET_FILE_ID,
        model=BASE_MODEL_ID,
        lora=True,
        lora_r=16,
    )

    print("FT_JOB_ID", job_resp.id)
    FT_JOB_ID = job_resp.id


message='Starting from together>=1.3.0, the default batch size is set to the maximum allowed value for each model.'
message='Starting from together>=1.3.0, the default batch size is set to the maximum allowed value for each model.'


FT_JOB_ID ft-49dc2cfb-959b


In [ ]:
from together.types.finetune import FinetuneJobStatus

status = None
while status != FinetuneJobStatus.STATUS_COMPLETED:
    ft_resp = client.fine_tuning.retrieve(FT_JOB_ID)
    status = ft_resp.status
    print(
        "status:",
        ft_resp.status,
        "steps_completed:",
        ft_resp.steps_completed,
        "output_name:",
        ft_resp.output_name,
        "events:",
        [event.message for event in ft_resp.events or []],
    )
    time.sleep(90)


status: FinetuneJobStatus.STATUS_PENDING steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_completed: 0 output_name: zackovits/DeepSeek-R1-Distill-Qwen-14B-77124c1f events: ['Fine tune request created']
status: FinetuneJobStatus.STATUS_QUEUED steps_compl